In [ ]:
from bs4 import BeautifulSoup
import requests, json, lxml
import pandas as pd
from statistics import mean
from collections import Counter
import nltk
nltk.download('stopwords')
nltk.download('punkt')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import re
import time
import timeit

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [ ]:
from google.colab import auth
import gspread
from google.auth import default
#autenticating to google
auth.authenticate_user()
creds, _ = default()
gc = gspread.authorize(creds)


In [ ]:
import pandas as pd
#defining my worksheet
worksheet = gc.open('Keywords').sheet1
#get_all_values gives a list of rows
rows = worksheet.get_all_values()
#Convert to a DataFrame
df = pd.DataFrame(rows)
df

0                                              1
0    No.                                        Keyword
1      1               How to maintain a healthy weight
2      2                Best exercises for heart health
3      3        Tips for lowering cholesterol naturally
4      4                 How to boost the immune system
..   ...                                            ...
146  146  Health guidelines for transgender individuals
147  147                Managing health with disability
148  148                 Nutrition tips for the elderly
149  149          Fitness routines for wheelchair users
150  150   Health considerations for pregnant teenagers

[151 rows x 2 columns]

In [ ]:
#creating columns name
df.columns = df.iloc[0]
df = df.iloc[1:]
df

0    No.                                        Keyword
1      1               How to maintain a healthy weight
2      2                Best exercises for heart health
3      3        Tips for lowering cholesterol naturally
4      4                 How to boost the immune system
5      5              Natural remedies for better sleep
..   ...                                            ...
146  146  Health guidelines for transgender individuals
147  147                Managing health with disability
148  148                 Nutrition tips for the elderly
149  149          Fitness routines for wheelchair users
150  150   Health considerations for pregnant teenagers

[150 rows x 2 columns]

In [ ]:
keywords = df.Keyword.values.tolist()
print(len(keywords), keywords)

150 ['How to maintain a healthy weight', 'Best exercises for heart health', 'Tips for lowering cholesterol naturally', 'How to boost the immune system', 'Natural remedies for better sleep', 'What are the early signs of diabetes?', 'How to manage high blood pressure', 'Symptoms of thyroid problems', 'Best diet for managing arthritis', 'How to treat acid reflux at home', 'How to have clear skin naturally', 'Best anti-aging skin care routines', 'How to reduce acne breakouts', 'Home remedies for dry skin', 'Tips for healthy hair and nails', 'How to reduce stress quickly', 'Techniques for managing anxiety', 'Best therapies for depression', 'How to deal with panic attacks', 'Signs of mental health issues', 'How to ease menstrual cramps', 'Pregnancy health tips', 'How to detect signs of breast cancer', 'Health tips for menopausal women', 'Best exercises during pregnancy', 'How to prevent male hair loss', 'Tips for prostate health', 'How to increase testosterone naturally', 'Health screenings 

In [ ]:
duplicated = df.loc[df.Keyword.duplicated(), :]
duplicated_list = duplicated['Keyword'].tolist()
print(duplicated_list)


[]


In [ ]:
keywords = df['Keyword'].loc[0:].tolist()
print(keywords)

['How to maintain a healthy weight', 'Best exercises for heart health', 'Tips for lowering cholesterol naturally', 'How to boost the immune system', 'Natural remedies for better sleep', 'What are the early signs of diabetes?', 'How to manage high blood pressure', 'Symptoms of thyroid problems', 'Best diet for managing arthritis', 'How to treat acid reflux at home', 'How to have clear skin naturally', 'Best anti-aging skin care routines', 'How to reduce acne breakouts', 'Home remedies for dry skin', 'Tips for healthy hair and nails', 'How to reduce stress quickly', 'Techniques for managing anxiety', 'Best therapies for depression', 'How to deal with panic attacks', 'Signs of mental health issues', 'How to ease menstrual cramps', 'Pregnancy health tips', 'How to detect signs of breast cancer', 'Health tips for menopausal women', 'Best exercises during pregnancy', 'How to prevent male hair loss', 'Tips for prostate health', 'How to increase testosterone naturally', 'Health screenings ever

**All used functions**

In [ ]:
headers = {
      "User-Agent": "Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/108.0.0.0 Safari/537.36"
  }

In [ ]:
def total_text_count(url):
  html = requests.get(url, headers=headers, verify=False, timeout=30)
  soup = BeautifulSoup(html.text, 'lxml')

  text = soup.get_text(strip=True)
  len_text = len(text.split())
  return len_text

def get_text_tag(url, tag):
  html = requests.get(url, headers=headers, verify=False, timeout=30)
  soup = BeautifulSoup(html.text, 'lxml')
  lst = []
  for el in soup.find_all(tag):
    lst.append(el.text.strip())
  avg_len = round(mean([len(i.split()) for i in lst]),2) if lst else None
  return lst, len(lst), avg_len




def keyword_counter(keyword, tag):
  counts = Counter()

  stop_words = set(stopwords.words('english'))
  word_tokens = word_tokenize((keyword).lower())
  filtered_sentence = [w for w in word_tokens if not w.lower() in stop_words]
  filtered_sentence = []
  for w in word_tokens:
    if w not in stop_words:
        filtered_sentence.append(w)

  for sentence in tag:
    if sentence:
      counts.update(word.strip('.,?!"\'').lower() for word in sentence.split())
    else:
      continue

  res = {key: counts[key] for key in counts.keys()
        & filtered_sentence}

  if not res:
    res = None
  return res




def link_keyword_counter(keyword, url):
  counts = Counter()

  stop_words = set(stopwords.words('english'))
  word_tokens = word_tokenize((keyword).lower())
  filtered_sentence = [w for w in word_tokens if not w.lower() in stop_words]
  filtered_sentence = []
  for w in word_tokens:
    if w not in stop_words:
        filtered_sentence.append(w)

  print(word_tokens)
  print(filtered_sentence)

  split_url = re.split('/|-|_|\.| ', url)

  for sentence in split_url:
    counts.update(word.strip('.,?!"\'').lower() for word in sentence.split())

  res = {key: counts[key] for key in counts.keys()
        & filtered_sentence}
  if not res:
    res = None
  return res





def links_counter(url):
  html = requests.get(url, headers=headers, verify=False, timeout=30)
  soup = BeautifulSoup(html.text, 'lxml')
  internalLinks = 0
  externalLinks = 0
  a_text = []
  links = soup.find_all("a") # Find all elements with the tag
  for l in links:
    link = l.get('href')
    if l.string:
      a_text.append(l.string)
    if link == None:
      continue
    if link.startswith(url) or link.startswith("/") or link.startswith("#") :
      internalLinks += 1
    else:
      externalLinks +=1

  return a_text, internalLinks, externalLinks




def metadesc_find(url, keyword):
  counts = Counter()
  keyword = (keyword).lower().split()
  html = requests.get(url, headers=headers, verify=False, timeout=30)
  soup = BeautifulSoup(html.text, 'lxml')
  desc = None
  desc_len = 0
  res = None

  for tag in soup.find_all("meta"):
      if tag.get("property", None) == "og:title":
          desc = tag.get("content", None)
          if desc:
            print(desc)
            desc_len = len(desc.split())
            counts.update(word.strip('.,?!"\'').lower() for word in desc.split())
            res = {key: counts[key] for key in counts.keys()
                  & keyword}
            print(res)
  return desc, desc_len, res




def image_alt_find(url):
  html = requests.get(url, headers=headers, verify=False, timeout=30)
  soup = BeautifulSoup(html.text, 'lxml')
  images = soup.find_all("img")
  #img_links = []
  img_alt = []
  i=0
  for image in images:
    #img_links.append(image.get("src"))
    if image.get("alt"):
      alt = image.get("alt").strip()
    else:
      alt = None
    img_alt.append(alt)
    i += 1
  return i, img_alt


**Main 🎠**

In [ ]:

data = []

for k in keywords:
  params = {
      "q": k,
      "hl": "en",
      "gl": "vn",
      "start": 0,
  }

  headers = {
      "User-Agent": "Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/108.0.0.0 Safari/537.36"
  }

  page_limit = 2

  page_num = 0

  i = 0
  while True:
      time.sleep(3)
      page_num += 1
      #print(f"page: {page_num}")
      html = requests.get("https://www.google.com/search", params=params, headers=headers, verify=False, timeout=30)
      html.raise_for_status()
      #print(html.url)
      soup = BeautifulSoup(html.text, 'lxml')


      for result in soup.select(".tF2Cxc"):
          time.sleep(3)
          i += 1
          if i == 11:
            break
          title = result.select_one(".DKV0Md").text
          try:
            snippet = result.select_one(".lEBKkf ").text.strip()
          except:
            snippet = None
          link = result.select_one(".yuRUbf a")["href"]
          print(link)
          try:
            total_words = total_text_count(link)

            h1_lst, h1_num, h1_len = get_text_tag(link, "h1")
            h2_lst, h2_num, h2_len = get_text_tag(link, "h2")
            h3_lst, h3_num, h3_len = get_text_tag(link, "h3")

            header_total = h1_num + h2_num + h3_num

            p_lst, p_num, p_len = get_text_tag(link, "p")

            footer_lst, footer_num, footer_len = get_text_tag(link, "footer")

            img_count, img_alt = image_alt_find(link)

            print(img_count, img_alt)

            a_text, internalLinks, externalLinks = links_counter(link)
            total_link = internalLinks + externalLinks

            h1_kcount = keyword_counter(k, h1_lst)
            h2_kcount = keyword_counter(k, h2_lst)
            h3_kcount = keyword_counter(k, h3_lst)

            p_kcount = keyword_counter(k, p_lst)

            a_kcount = keyword_counter(k, a_text)

            footer_kcount = keyword_counter(k, footer_lst)

            link_kcount = link_keyword_counter(k, link)

            imalt_kcount = keyword_counter(k, img_alt)

            meta_desc, meta_desc_len, meta_kcount = metadesc_find(link, k)

            ti_lst, ti_num, ti_len = get_text_tag(link, "title")
            if ti_lst:
              ti_lst = 1
            else:
              ti_lst = 0

            data.append({
              "keyword": k,
              "rank": i,
              "title": title,
              "snippet": snippet,
              "link": link,
              "total_words": total_words,
              "h1_num": h1_num,
              "h1_len": h1_len,
              "h2_num": h2_num,
              "h2_len": h2_len,
              "h3_num": h3_num,
              "h3_len": h3_len,
              "header_total": header_total,
              "img_count": img_count,
              "internalLinks": internalLinks,
              "externalLinks": externalLinks,
              "total_link": total_link,
              "h1_kcount": h1_kcount,
              "h2_kcount": h2_kcount,
              "h3_kcount": h3_kcount,
              "p_kcount": p_kcount,
              "a_kcount": a_kcount,
              "footer_kcount": footer_kcount,
              "link_kcount": link_kcount,
              "imalt_kcount": imalt_kcount,
              "meta_desc_len": meta_desc_len,
              "meta_kcount": meta_kcount,
              "ti_used": ti_lst

            })
          except requests.exceptions.RequestException as err:
              print ("OOps: Something Else",err)
          except requests.exceptions.HTTPError as errh:
              print ("Http Error:",errh)
          except requests.exceptions.ConnectionError as errc:
              print ("Error Connecting:",errc)
          except requests.exceptions.Timeout as errt:
              print ("Timeout Error:",errt)

      if page_num == page_limit:
          break
      if soup.select_one(".d6cvqb a[id=pnnext]"):
          params["start"] += 10
      else:
          break
dt_tb =  pd.DataFrame.from_dict(data)
dt_tb


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.google.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


https://www.nhlbi.nih.gov/health/educational/lose_wt/index.htm


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.nhlbi.nih.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.nhlbi.nih.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.nhlbi.nih.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpoo

16 ['U.S. flag', None, None, None, 'Skip left side navigation and go to content', 'Aim for a Healthy Weight', 'Apple with tape measure wrapped around it and dumb bells sitting on a scale.', 'Cover of Aim for a Healthy Weight booklet', 'back to top arrow', 'chat bubbles', 'email', 'National Heart, Lung, and Blood Home', 'Facebook', 'Twitter', 'Youtube', 'LinkedIn']


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.nhlbi.nih.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


...

15 ["Nationwide Children's Hospital Logo", 'no image', 'NICU Baby in Isolette', "Nationwide Children's Hospital Patient Stock Photo", 'Thinking of You', 'no image', 'mother and daughter sitting at table outside.', 'Sarah Saxbe', 'teen boy and teen girl walking and talking together', 'image of boy hugging his pregnant mother', 'teens talking with their phones in their hands', 'squirrel', 'ANCC Magnet Award Logo', 'US News Honor Roll 2020-21', "Forbes 2024 America's Best Large Employers"]


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.nationwidechildrens.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


['health', 'considerations', 'for', 'pregnant', 'teenagers']
['health', 'considerations', 'pregnant', 'teenagers']


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.nationwidechildrens.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.nationwidechildrens.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


keyword  rank  \
0                 How to maintain a healthy weight     1   
1                 How to maintain a healthy weight     2   
2                 How to maintain a healthy weight     3   
3                 How to maintain a healthy weight     4   
4                 How to maintain a healthy weight     5   
...                                            ...   ...   
1422  Health considerations for pregnant teenagers     6   
1423  Health considerations for pregnant teenagers     7   
1424  Health considerations for pregnant teenagers     8   
1425  Health considerations for pregnant teenagers     9   
1426  Health considerations for pregnant teenagers    10   

                                                  title snippet  \
0                     Maintain a Healthy Weight - NHLBI    None   
1     Maintaining a Healthy Weight | National Instit...    None   
2                       About Healthy Weight and Growth    None   
3                     Tips to Maintain a Healthy Weight    None   
4                         Keeping a Healthy Body Weight    None   
...                                                 ...     ...   
1422                 Health risk of teenage pregnancies    None   
1423  How to ramp up your coverage of teen pregnancy...    None   
1424               Teen Pregnancy Issues and Challenges    None   
1425           Learn The Health Risks Of Teen Pregnancy    None   
1426                            Risks of Teen Pregnancy    None   

                                                   link  total_words  h1_num  \
0     https://www.nhlbi.nih.gov/health/educational/l...          603       7   
1     https://www.nia.nih.gov/health/healthy-eating-...         1402       1   
2     https://www.cdc.gov/healthy-weight-growth/abou...          953       1   
3     https://reverehealth.com/live-better/tips-to-m...          974       1   
4     https://www.heart.org/en/healthy-living/health...          924       1   
...                                                 ...          ...     ...   
1422  https://www.solidarmed.ch/en/news/health-risk-...         1717       1   
1423  https://healthjournalism.org/blog/2023/09/how-...         1162       1   
1424  https://americanpregnancy.org/unplanned-pregna...         3220       1   
1425  https://merrionultrasound.ie/teen-pregnancy-he...          775       5   
1426  https://www.nationwidechildrens.org/family-res...         2789       1   

      h1_len  h2_num  h2_len  ...                                   h2_kcount  \
0        5.0       3    3.00  ...                                        None   
1        4.0      10    7.10  ...  {'healthy': 4, 'maintain': 1, 'weight': 6}   
2        5.0      11    2.73  ...                 {'healthy': 3, 'weight': 2}   
3        6.0       4   20.00  ...               {'healthy': 1, 'maintain': 1}   
4        5.0      13    3.77  ...                 {'healthy': 2, 'weight': 2}   
...      ...     ...     ...  ...                                         ...   
1422     4.0       8    6.75  ...                               {'health': 1}   
1423    11.0      12    1.50  ...                                        None   
1424     5.0       3    4.00  ...                             {'pregnant': 1}   
1425     5.6       1    6.00  ...                                        None   
1426     4.0       1    6.00  ...                                        None   

                        h3_kcount  \
0                            None   
1                            None   
2                            None   
3                            None   
4     {'healthy': 1, 'weight': 1}   
...                           ...   
1422                {'health': 2}   
1423                         None   
1424              {'pregnant': 1}   
1425                         None   
1426                         None   

                                           p_kcount  \
0      {'healthy': 11, 'maintain': 4, 'weight': 13}   
1      {'healthy': 11, 'main

In [ ]:
dt_tb =  pd.DataFrame.from_dict(data)
dt_tb

keyword  rank  \
0                 How to maintain a healthy weight     1   
1                 How to maintain a healthy weight     2   
2                 How to maintain a healthy weight     3   
3                 How to maintain a healthy weight     4   
4                 How to maintain a healthy weight     5   
...                                            ...   ...   
1422  Health considerations for pregnant teenagers     6   
1423  Health considerations for pregnant teenagers     7   
1424  Health considerations for pregnant teenagers     8   
1425  Health considerations for pregnant teenagers     9   
1426  Health considerations for pregnant teenagers    10   

                                                  title snippet  \
0                     Maintain a Healthy Weight - NHLBI    None   
1     Maintaining a Healthy Weight | National Instit...    None   
2                       About Healthy Weight and Growth    None   
3                     Tips to Maintain a Healthy Weight    None   
4                         Keeping a Healthy Body Weight    None   
...                                                 ...     ...   
1422                 Health risk of teenage pregnancies    None   
1423  How to ramp up your coverage of teen pregnancy...    None   
1424               Teen Pregnancy Issues and Challenges    None   
1425           Learn The Health Risks Of Teen Pregnancy    None   
1426                            Risks of Teen Pregnancy    None   

                                                   link  total_words  h1_num  \
0     https://www.nhlbi.nih.gov/health/educational/l...          603       7   
1     https://www.nia.nih.gov/health/healthy-eating-...         1402       1   
2     https://www.cdc.gov/healthy-weight-growth/abou...          953       1   
3     https://reverehealth.com/live-better/tips-to-m...          974       1   
4     https://www.heart.org/en/healthy-living/health...          924       1   
...                                                 ...          ...     ...   
1422  https://www.solidarmed.ch/en/news/health-risk-...         1717       1   
1423  https://healthjournalism.org/blog/2023/09/how-...         1162       1   
1424  https://americanpregnancy.org/unplanned-pregna...         3220       1   
1425  https://merrionultrasound.ie/teen-pregnancy-he...          775       5   
1426  https://www.nationwidechildrens.org/family-res...         2789       1   

      h1_len  h2_num  h2_len  ...                                   h2_kcount  \
0        5.0       3    3.00  ...                                        None   
1        4.0      10    7.10  ...  {'healthy': 4, 'maintain': 1, 'weight': 6}   
2        5.0      11    2.73  ...                 {'healthy': 3, 'weight': 2}   
3        6.0       4   20.00  ...               {'healthy': 1, 'maintain': 1}   
4        5.0      13    3.77  ...                 {'healthy': 2, 'weight': 2}   
...      ...     ...     ...  ...                                         ...   
1422     4.0       8    6.75  ...                               {'health': 1}   
1423    11.0      12    1.50  ...                                        None   
1424     5.0       3    4.00  ...                             {'pregnant': 1}   
1425     5.6       1    6.00  ...                                        None   
1426     4.0       1    6.00  ...                                        None   

                        h3_kcount  \
0                            None   
1                            None   
2                            None   
3                            None   
4     {'healthy': 1, 'weight': 1}   
...                           ...   
1422                {'health': 2}   
1423                         None   
1424              {'pregnant': 1}   
1425                         None   
1426                         None   

                                           p_kcount  \
0      {'healthy': 11, 'maintain': 4, 'weight': 13}   
1      {'healthy': 11, 'main

In [ ]:
from google.colab import drive
drive.mount('drive', force_remount=True)

dt_tb.to_csv('/content/drive/My Drive/seo_scraped_data.csv', encoding='utf-8', mode='a', index= False, header=False)

Mounted at drive


In [ ]:
#find duplicates
from google.colab import drive
drive.mount('drive', force_remount=True)

import pandas as pd
result_scrape = pd.read_csv('/content/drive/My Drive/search_scraped_data.csv')
#for d in duplicated_list:
find_re = result_scrape.loc[result_scrape['keyword'] == duplicated_list[10]]
find_re


Mounted at drive


FileNotFoundError: [Errno 2] No such file or directory: '/content/drive/My Drive/search_scraped_data.csv'